In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import scipy.stats as st
from ydata_profiling import ProfileReport
from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import (OneHotEncoder,
                                   MinMaxScaler, 
                                   OrdinalEncoder)
from sklearn.pipeline import Pipeline
from sklearn.model_selection import (GridSearchCV, 
                                     RandomizedSearchCV)

In [2]:
data_samp = pd.read_csv('./datasets/kaggle_startups_sample_submit_28062024.csv')

In [3]:
data_test = pd.read_csv('./datasets/kaggle_startups_test_28062024.csv')

In [4]:
data_train = pd.read_csv('./datasets/kaggle_startups_train_28062024.csv')

In [5]:
data_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 52516 entries, 0 to 52515
Data columns (total 13 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   name               52515 non-null  object 
 1   category_list      50051 non-null  object 
 2   funding_total_usd  42447 non-null  float64
 3   status             52516 non-null  object 
 4   country_code       47014 non-null  object 
 5   state_code         45753 non-null  object 
 6   region             46157 non-null  object 
 7   city               46157 non-null  object 
 8   funding_rounds     52516 non-null  int64  
 9   founded_at         52516 non-null  object 
 10  first_funding_at   52516 non-null  object 
 11  last_funding_at    52516 non-null  object 
 12  closed_at          4917 non-null   object 
dtypes: float64(1), int64(1), object(11)
memory usage: 5.2+ MB


In [6]:
ProfileReport(data_samp, title="Profiling Report Samp")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

В датафрейме samp хранятся значения таргета, имя - статус, никаких проблем, тут всё ок. 

Нужно будет совместить пропуски(если они будут в трейне и тесте), удалить или заполнить. решу позже.

In [7]:
ProfileReport(data_train, title="Profiling Report")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Data_train:
- ***надо чекнуть на дубли***
1) name 
- 1 пропущенный 
- медианная длина названия 62 символа
2) category_list
- 2465 пропусков (4.7%)
- самые частые категории software (4.7%), biotechnology(2.7%), health(2.2%), media (2.1%)
3) funding_round_total
- 10069(19.2%) пропущены 
- среднее 18.247.481
- медиана 2.000.000
- 50% значений находятся в диапазоне от 336027.5 до 10.000.000
- IQR 9.663.972
- стандартное отклонение 1.87* 10^8
- есть очень большие значения,их мало, уберу их ниже
4) status тут все ок
5) country code 
- пропусков 10.5%(5502)
- самая часта usa( 63.2%)
6) state code 
- 6763(12.9%) пропущено
- самое частое : ca(10219),ny(3112),ma(2020),tx(1562)
7) region 
- 6359(12.1%) пропусков
8) city
- 
9) funding rounds
- мин : 1, макс: 19
- бОльшая часть компаний имеет до 5 раундов
10) founded_at
- распределение с длинным левым концом, что говорит нам о том, что есть ряд компаний «старожил», большая же часть компаний была основана с 1998 по 2018
11) first_funding_at
- ситуация аналогична с founded at
12) last_funding_at
- ситуация аналогична c first_funding_at
13) closed_at
- распределение с exp ростом, с явным куполом в диапазоне 2008 - 2018
(основной срок закрытия , начиная скризиса и по последующие дни, исправив пропуски в этмо столцбе, количество компаний, закрывшихся 01-01-2018 увеличится, но исходная картина описанадо этого)

In [8]:
ProfileReport(data_test, title="Profiling Report")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

data_test:
- ***надо чекнуть на дубли***
1) name 
- пропусков нет
2) category_list
- 591 пропусков (4.5%)
- самые частые категории software (1217 4.6%), biotechnology (693 2.6%), health (589 2.2%), media (574 2.2%)
3) funding_round_total
- 2578(19.6%) пропущены 
- среднее 16.549.103
- медиана 2.000.000
- 50% значений находятся в диапазоне от 320000 до 10000000
- IQR 9.680.000
- стандартное отклонение 92.172.826
- есть очень большие значения,их мало, уберу их ниже(заполню медианой по их первой категории)
4) country code 
- пропусков 10.5%(1382)
- самая часта usa	(7428	63.3%)
6) state code 
- 1695(12.5%) пропущено
- самое частое : ca(10219),ny(3112),ma(2020),tx(1562)
7) region 
- 1589(12.1%) пропусков
8) city
- 1587(12.1%) пропусков
9) funding rounds
- мин : 1, макс: 19
- бОльшая часть компаний имеет до 5 раундов
10) founded_at
- распределение с длинным левым концом, что говорит нам о том, что есть ряд компаний «старожил», большая же часть компаний была основана с 1998 по 2018
11) first_funding_at
- ситуация аналогична с founded at
12) last_funding_at
- ситуация аналогична c first_funding_at
13) lifetime
- descr = (длительность жизни в днях, по - сути, это дата коцна - дата начала)
- смещение с длинным правым концом говорит о том, что лишь небольшое число компаний живут долго ( предположу, что их "капитализация" больше остальных)
- медиана 2526 дней
- среднее 3098 дней
- 50% компаний живут от 1726 до 3866 дней

**Дубликаты по train / test**

In [55]:
# Список столбцов тренировочного датасета
train_col_names = list(data_train.columns)
# Список датафреймов (тренировочный и тестовый)
data_names = dict(data_train = data_train, data_test = data_test)

In [51]:
data_train['name'].duplicated().sum()

0

In [52]:
data_test['name'].duplicated().sum()

0

In [53]:
data_train.duplicated().sum()

0

In [54]:
data_test.duplicated().sum()

0

Явных удблей нет, все остальные колонки нет смысла смотреть, позже после преобразвоания данных проверим еще ра на явные дубли, для корректности merg'а